In [2]:
import pandas as pd
import numpy as np
from tqdm import tqdm

# Load the dataset
file_path = 'binding_sites_uniprot_16M.tsv'
data = pd.read_csv(file_path, sep='\t')

# Display the first few rows of the dataframe
#data.head()

# Filter out rows with NaN values in the 'Protein families' column
data = data[pd.notna(data['Protein families'])]

# Display the first few rows of the modified dataframe
#data.head()

# Group the data by 'Protein families' and get the size of each group
family_sizes = data.groupby('Protein families').size()

# Create a new column with the size of each family
data['Family size'] = data['Protein families'].map(family_sizes)

# Sort the data by 'Family size' in descending order and then by 'Protein families'
data_sorted = data.sort_values(by=['Family size', 'Protein families'], ascending=[False, True])

# Drop the 'Family size' column as it is no longer needed
data_sorted.drop(columns='Family size', inplace=True)

# Define a function to extract the location from the binding and active site columns
def extract_location(site_info):
    if pd.isnull(site_info):
        return None
    locations = []
    for info in site_info.split(';'):
        if 'BINDING' in info or 'ACT_SITE' in info:
            locations.append(info.split()[1])
    return '; '.join(locations)

# Apply the function to the 'Binding site' and 'Active site' columns to extract the locations
data_sorted['Binding site'] = data_sorted['Binding site'].apply(extract_location)
data_sorted['Active site'] = data_sorted['Active site'].apply(extract_location)

# Display the first few rows of the modified dataframe
#data_sorted.head()

# Create a new column that combines the 'Binding site' and 'Active site' columns
data_sorted['Binding-Active site'] = data_sorted['Binding site'].astype(str) + '; ' + data_sorted['Active site'].astype(str)

# Replace 'nan' values with None
data_sorted['Binding-Active site'] = data_sorted['Binding-Active site'].replace('nan; nan', None)

# Display the first few rows of the updated dataframe
#data_sorted.head()

# Find entries in the "Binding-Active site" column containing '<' or '>'
entries_with_angle_brackets = data_sorted['Binding-Active site'].str.contains('<|>', na=False)

# Get the number of such entries
num_entries_with_angle_brackets = entries_with_angle_brackets.sum()

# Display the number of entries containing '<' or '>'
print(f"Number of entries with angle brackets: {num_entries_with_angle_brackets}")

# Remove all rows where the "Binding-Active site" column contains '<' or '>'
data_filtered = data_sorted[~entries_with_angle_brackets]

# Get the number of remaining rows
num_remaining_rows = data_filtered.shape[0]

# Display the number of remaining rows
print(f"Number of remaining rows: {num_remaining_rows}")

# Get the number of distinct protein families
num_distinct_families = data_filtered['Protein families'].nunique()

# Display the number of distinct protein families
print(f"Number of distinct protein families: {num_distinct_families}")

# Define the target number of rows for the test set (approximately 20% of the data)
target_test_rows = int(0.20 * num_remaining_rows)

# Get unique protein families
unique_families = data_filtered['Protein families'].unique()

# Shuffle the unique families to randomize the selection
np.random.shuffle(unique_families)

# Group the data by 'Protein families' to facilitate faster family-wise selection
grouped_data = data_filtered.groupby('Protein families')

# Initialize variables to keep track of the selected rows for the test and train sets
test_rows = []
current_test_rows = 0

# Initialize a flag to indicate whether the threshold has been crossed
threshold_crossed = False

# Initialize a variable to keep track of the previous family
previous_family = None

# Loop through the shuffled families and add rows to the test set until we reach the target number of rows
for family in tqdm(unique_families, unit="family"):
    family_rows = grouped_data.get_group(family).index.tolist()
    # If the threshold is not yet crossed, or the family is the same as the previous family, add the family to the test set
    if not threshold_crossed or (previous_family == family):
        test_rows.extend(family_rows)
        current_test_rows += len(family_rows)
        previous_family = family  # Keep track of the previous family
    # Check if the threshold is crossed with the addition of the current family
    if current_test_rows >= target_test_rows:
        threshold_crossed = True  # Set the flag to True once the threshold is crossed

# Get the indices of the rows for the train set (all rows not in the test set) using set operations for efficiency
train_rows = set(data_filtered.index) - set(test_rows)

# Create the test and train datasets using loc indexer with list of indices
test_df = data_filtered.loc[list(test_rows)]
train_df = data_filtered.loc[list(train_rows)]

# Print the number of distinct protein families in the test and train sets
num_test_families = test_df['Protein families'].nunique()
num_train_families = train_df['Protein families'].nunique()
print(f"Number of distinct protein families in the test set: {num_test_families}")
print(f"Number of distinct protein families in the train set: {num_train_families}")
percentage = num_test_families/(num_test_families+num_train_families)
print(f"Percentage of families in test set: {percentage}")

test_df.shape[0], train_df.shape[0]


Number of entries with angle brackets: 35
Number of remaining rows: 16460737
Number of distinct protein families: 10258


100%|██████████| 10258/10258 [00:04<00:00, 2232.02family/s]


Number of distinct protein families in the test set: 2076
Number of distinct protein families in the train set: 8182
Percentage of families in test set: 0.20237863131214662


(3307395, 13153342)

In [3]:
# Get the unique families in the test and train datasets
unique_test_families = set(test_df['Protein families'].unique())
unique_train_families = set(train_df['Protein families'].unique())

# Find the common families between the test and train datasets
common_families = unique_test_families.intersection(unique_train_families)

# Output the common families and their count
print(f"Number of common families: {len(common_families)}")
if len(common_families) > 0:
    print(f"Common families: {common_families}")
else:
    print("No common families between test and train datasets.")


Number of common families: 0
No common families between test and train datasets.


In [4]:
import re

# Find rows where the "Binding-Active site" column contains the character "?", treating "?" as a literal character
test_rows_with_question_mark = test_df[test_df['Binding-Active site'].str.contains('\?', na=False, regex=True)]
train_rows_with_question_mark = train_df[train_df['Binding-Active site'].str.contains('\?', na=False, regex=True)]

# Get the number of such rows in both datasets
num_test_rows_with_question_mark = len(test_rows_with_question_mark)
num_train_rows_with_question_mark = len(train_rows_with_question_mark)

print(f"Number of test rows with question mark: {num_test_rows_with_question_mark}")
print(f"Number of train rows with question mark: {num_train_rows_with_question_mark}")

# Delete the rows containing '?' in the "Binding-Active site" column
test_df = test_df.drop(test_rows_with_question_mark.index)
train_df = train_df.drop(train_rows_with_question_mark.index)

# Check the number of remaining rows in both datasets
remaining_test_rows = test_df.shape[0]
remaining_train_rows = train_df.shape[0]

print(f"Number of remaining test rows: {remaining_test_rows}")
print(f"Number of remaining train rows: {remaining_train_rows}")

def expand_ranges(s):
    """Expand ranges in a string."""
    return re.sub(r'(\d+)\.\.(\d+)', lambda m: ', '.join(map(str, range(int(m.group(1)), int(m.group(2))+1))), str(s))

# Apply the function to expand ranges in the "Binding-Active site" column in both datasets
test_df['Binding-Active site'] = test_df['Binding-Active site'].apply(expand_ranges)
train_df['Binding-Active site'] = train_df['Binding-Active site'].apply(expand_ranges)


Number of test rows with question mark: 0
Number of train rows with question mark: 2
Number of remaining test rows: 3307395
Number of remaining train rows: 13153340


In [5]:
def convert_to_binary_list(binding_active_str, sequence_len):
    """Convert a Binding-Active site string to a binary list based on the sequence length."""
    # Step 2: Create a list of 0s with length equal to the sequence length
    binary_list = [0] * sequence_len
    
    # Step 3: Retrieve the indices and set the corresponding positions to 1
    if pd.notna(binding_active_str):
        # Get the indices from the binding-active site string
        indices = [int(x) - 1 for segment in binding_active_str.split(';') for x in segment.split(',') if x.strip().isdigit()]
        for idx in indices:
            # Ensure the index is within the valid range
            if 0 <= idx < sequence_len:
                binary_list[idx] = 1
                
    # Step 4: Return the binary list
    return binary_list

# Apply the function to both datasets
test_df['Binding-Active site'] = test_df.apply(lambda row: convert_to_binary_list(row['Binding-Active site'], len(row['Sequence'])), axis=1)
train_df['Binding-Active site'] = train_df.apply(lambda row: convert_to_binary_list(row['Binding-Active site'], len(row['Sequence'])), axis=1)


In [6]:
test_df.head()

Entry                                   Protein families  \
791321   A0A0C2CBT0  TDD superfamily, TSR3 family; Protein kinase s...   
1008964  A0A0N4V212  TDD superfamily, TSR3 family; Protein kinase s...   
1009019  A0A0N4XGU1  TDD superfamily, TSR3 family; Protein kinase s...   
1837901  A0A1I8B1G5  TDD superfamily, TSR3 family; Protein kinase s...   
5447097  A0A6V7USP8  TDD superfamily, TSR3 family; Protein kinase s...   

          Binding site Active site  \
791321   275; 323; 346        None   
1008964  131; 179; 202        None   
1009019   73; 121; 178        None   
1837901    40; 88; 111        None   
5447097   61; 109; 132        None   

                                                  Sequence  \
791321   MFDVFSGHNDAVLCVQYRDQESLAVSGSADNSIKCWDTRTGRPEMT...   
1008964  MVGYGVRARASGYHGRSKFRVKNKRKADKSYAENVSELAADSSRAI...   
1009019  MGKKGREQHGNKRTNKSRHADAGDAEPLSSHGEEDSESLDESRDDH...   
1837901  MASTDSSQSSDEDAKVEKAKKMPCILAMFDFGQCDPKRCSGRKLCR...   
5447097  MLFMVVPVLIMMQVDVVAIKKMTNTDSSESSGDDAVDDKSKKMPCI...   

                                       Binding-Active site  
791321   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
1008964  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
1009019  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
1837901  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
5447097  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...

In [7]:
train_df.head()

Entry                                   Protein families  \
1  A0A009GI32  3-hydroxyacyl-CoA dehydrogenase family; Enoyl-...   
3  A0A009HWM5  3-hydroxyacyl-CoA dehydrogenase family; Enoyl-...   
4  A0A009I6Q1  3-hydroxyacyl-CoA dehydrogenase family; Enoyl-...   
7  A0A009NCR4  3-hydroxyacyl-CoA dehydrogenase family; Enoyl-...   
9  A0A009QK39  3-hydroxyacyl-CoA dehydrogenase family; Enoyl-...   

                                  Binding site Active site  \
1  298; 326; 345; 402..404; 409; 431; 455; 502         452   
3  298; 326; 345; 402..404; 409; 431; 455; 502         452   
4  298; 326; 345; 402..404; 409; 431; 455; 502         452   
7  298; 326; 345; 402..404; 409; 431; 455; 502         452   
9  298; 326; 345; 402..404; 409; 431; 455; 502         452   

                                            Sequence  \
1  MIHAGNAITVQMLADGIAEFRFDLQGESVNKFNRATIEDFKAAIAA...   
3  MIHAGNAITVQMLADGIAEFRFDLQGESVNKFNRATIEDFKAAIAA...   
4  MIHAGNAITVQMLSDGIAEFRFDLQGESVNKFNRATIEDFQAAIAA...   
7  MIHAGNAITVQMLSDGIAEFRFDLQGESVNKFNRATIEDFQAAIAA...   
9  MIHAGNAITVQMLADGIAEFRFDLQGESVNKFNRATIEDFKAAIAA...   

                                 Binding-Active site  
1  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
3  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
4  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
7  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
9  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...

In [8]:
import pickle
import random

def split_into_chunks(sequences, labels):
    """Split sequences and labels into chunks of size 1000 or less."""
    chunk_size = 1000
    new_sequences = []
    new_labels = []
    
    for seq, lbl in zip(sequences, labels):
        if len(seq) > chunk_size:
            # Split the sequence and labels into chunks of size 1000 or less
            for i in range(0, len(seq), chunk_size):
                new_sequences.append(seq[i:i+chunk_size])
                new_labels.append(lbl[i:i+chunk_size])
        else:
            new_sequences.append(seq)
            new_labels.append(lbl)
            
    return new_sequences, new_labels

# Extract the necessary columns to create lists of sequences and labels
test_sequences_by_family = test_df['Sequence'].tolist()
test_labels_by_family = test_df['Binding-Active site'].tolist()
train_sequences_by_family = train_df['Sequence'].tolist()
train_labels_by_family = train_df['Binding-Active site'].tolist()

# Get the number of samples in each dataset
num_test_samples = len(test_sequences_by_family)
num_train_samples = len(train_sequences_by_family)

# Define the percentage of data you want to keep
percentage_to_keep = 100  # for keeping 6.00% of the data

# Generate random indices representing a percentage of each dataset
random_test_indices = random.sample(range(num_test_samples), int(num_test_samples * (percentage_to_keep / 100)))
random_train_indices = random.sample(range(num_train_samples), int(num_train_samples * (percentage_to_keep / 100)))

# Create smaller datasets using the random indices
test_sequences_small = [test_sequences_by_family[i] for i in random_test_indices]
test_labels_small = [test_labels_by_family[i] for i in random_test_indices]
train_sequences_small = [train_sequences_by_family[i] for i in random_train_indices]
train_labels_small = [train_labels_by_family[i] for i in random_train_indices]

# Apply the function to create new datasets with chunks of size 1000 or less
test_sequences_chunked, test_labels_chunked = split_into_chunks(test_sequences_small, test_labels_small)
train_sequences_chunked, train_labels_chunked = split_into_chunks(train_sequences_small, train_labels_small)

# Paths to save the new chunked pickle files
test_labels_chunked_path = '16M_data/test_labels_chunked_by_family.pkl'
test_sequences_chunked_path = '16M_data/test_sequences_chunked_by_family.pkl'
train_labels_chunked_path = '16M_data/train_labels_chunked_by_family.pkl'
train_sequences_chunked_path = '16M_data/train_sequences_chunked_by_family.pkl'

# Save the chunked datasets as new pickle files
with open(test_labels_chunked_path, 'wb') as file:
    pickle.dump(test_labels_chunked, file)
with open(test_sequences_chunked_path, 'wb') as file:
    pickle.dump(test_sequences_chunked, file)
with open(train_labels_chunked_path, 'wb') as file:
    pickle.dump(train_labels_chunked, file)
with open(train_sequences_chunked_path, 'wb') as file:
    pickle.dump(train_sequences_chunked, file)

test_labels_chunked_path, test_sequences_chunked_path, train_labels_chunked_path, train_sequences_chunked_path


('065_data/test_labels_chunked_by_family.pkl',
 '065_data/test_sequences_chunked_by_family.pkl',
 '065_data/train_labels_chunked_by_family.pkl',
 '065_data/train_sequences_chunked_by_family.pkl')

In [9]:
# Load each pickle file and get the number of entries in each
with open(test_labels_chunked_path, 'rb') as file:
    test_labels_chunked = pickle.load(file)
    num_test_labels_chunked = len(test_labels_chunked)

with open(test_sequences_chunked_path, 'rb') as file:
    test_sequences_chunked = pickle.load(file)
    num_test_sequences_chunked = len(test_sequences_chunked)

with open(train_labels_chunked_path, 'rb') as file:
    train_labels_chunked = pickle.load(file)
    num_train_labels_chunked = len(train_labels_chunked)

with open(train_sequences_chunked_path, 'rb') as file:
    train_sequences_chunked = pickle.load(file)
    num_train_sequences_chunked = len(train_sequences_chunked)

num_test_labels_chunked, num_test_sequences_chunked, num_train_labels_chunked, num_train_sequences_chunked


(220620, 220620, 890637, 890637)